In [17]:
from datascienceutils import analyze
from datascienceutils import features
from datascienceutils.features import nlp
from datascienceutils import plotter

import pandas as pd
import numpy as np
import bokeh
from bokeh.plotting import output_notebook
output_notebook(bokeh.resources.INLINE)

%matplotlib inline

Loading BokehJS ...

In [18]:

max_topics = 8
def read_input(filename):
    with open(filename, 'r') as fd:
        inputs = fd.readlines()
    num_docs = int(inputs.pop(0))
    assert len(inputs) == num_docs
    return [nlp.filter_letters_only(each.strip('\n')) for each in inputs]

In [19]:
input_docs = [each.split(' ') for each in read_input('./trainingdata.txt')]
input_docs = [nlp.filter_stop_words(each) for each in input_docs]

In [ ]:
model = features.nlp.word_2_vector(input_docs, hs=1, negative=0)


In [ ]:
df = pd.DataFrame()
from scipy import spatial
import itertools

def get_sent_vector(sent):
    vectors = list()
    for word in sent:
        if word in model.wv.vocab:
            vectors.append(model[word])
    print(vectors)
    return np.mean(vectors, axis=0)
df['id'] = pd.Series(range(len(input_docs)))
df['score'] = model.score(input_docs)
df['doc_vector'] = [get_sent_vector(doc) for doc in input_docs]

[array([-0.1265676 ,  0.82583666,  0.38184047,  0.52319515,  0.40381116,
        0.17325285,  0.06262349, -0.16042194, -0.16128017,  0.03631723,
       -0.91018742,  0.06549168,  0.18460868,  0.18542267, -0.10584968,
       -0.09128166,  0.67496014,  0.30607301,  0.10300761,  0.22920689,
        0.4631919 , -1.05642784,  0.54696733, -0.19082391,  0.40801227,
       -0.33930746,  0.38646185, -0.28338015, -0.09617899, -0.02758302,
        0.74350601, -1.39644778, -0.41587558, -0.63559484, -0.18185912,
       -0.52207243,  0.36908466,  0.65321392, -0.38692102,  0.14237878,
       -0.05731273, -0.2103563 , -0.04349443, -0.13270365, -0.10992478,
       -0.41448709,  0.36689132, -0.1071942 , -0.43521914, -0.20151119,
       -0.05015378, -0.04119664, -0.54739016,  0.44541278,  0.1093624 ,
       -0.00973949, -0.51153511,  0.34243062, -0.60626894, -0.95251024,
       -0.48711935, -0.52597821,  0.19858025, -0.11890702,  1.09442782,
        0.05282705, -0.2913661 , -0.18306097, -0.7640478 , -0.7

In [ ]:
plotter.show(analyze.dist_analyze(df, 'score'))

In [ ]:
# Based on this flowchart http://scikit-learn.org/stable/tutorial/machine_learning_map/ for unsupervised clustering, 
# we can use either k-means or spectral clustering
analyze.silhouette_analyze(df, cluster_type='spectral')

In [ ]:
analyze.silhouette_analyze(df, cluster_type='kmeans')

In [ ]:
df.head()

In [ ]:
import sompy as sp
factory = sp.SOMFactory()
sm = factory.build(tfidfFeatures, mapsize=(10,10),normalization='var', initialization='pca')
sm.train(n_job=6, verbose='INFO')


In [ ]:
v=sompy.mapview.View2DPacked(50,50, 'test', text_size=8)
v.show(sm, what='codebook', cmap='jet', col_sz=6)
v.show(sm, what='cluster', cmap='jet', col_sz=6)

h = sompy.hitmap.HitMapView(10, 10, 'hitmap', text_size=8, show_text=True)
h.show(sm)